In [1]:
import pandas as pd
import useful_functions as use
from fuzzywuzzy import fuzz
import usaddress
from datetime import date

C:\Users\vigrose\AppData\Local\Continuum\anaconda3\lib\site-packages\fuzzywuzzy\fuzz.py:11: UserWarning: Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning
  warnings.warn('Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning')


In [3]:
path = '../../Data/PhoneAppend'
bolo_file = use.get_newest(path, 'BOLO_Address')
bolos = pd.read_csv(bolo_file, sep='|')
bolos['ME'] = use.fix_me(bolos['me#'])
bolos = bolos.fillna('None')

C:\Users\vigrose\AppData\Local\Continuum\anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3058: DtypeWarning: Columns (11) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [4]:
path = '../../Data/DataGov'
phones_file = use.get_newest(path, 'PhysicianCompare')
og_file = use.get_newest(path, 'DAC_National')

In [5]:
gov = pd.read_csv(og_file, encoding='latin', low_memory=False)
gov.columns = [c.strip() for c in gov.columns.values]
gov['NPI'] = [str(int(x)) for x in gov.NPI]
gov['ME'] = use.fix_me(gov.ME)

In [6]:
npi_me = use.get_npi_to_me()

In [7]:
phones = pd.read_csv(phones_file, encoding='latin', low_memory=False)
phones.columns = [c.strip() for c in phones.columns.values]
phones['NPI'] = [str(int(x)) for x in phones.NPI]
phones = pd.merge(phones, npi_me, on='NPI')
phoney = phones[['ME','adrs_id','phn_numbr','NPI']].drop_duplicates()

In [8]:
def is_a_match(thing_1, thing_2, threshold):
    if thing_1 == thing_2:
        match = True
    elif thing_1 in thing_2:
        match = True
    elif thing_2 in thing_1:
        match = True
    elif fuzz.ratio(thing_1, thing_2)>threshold:
        match = True
        print('')
        print(fuzz.ratio(thing_1, thing_2))
        print('------------------------------------')
    else:
        match = False
    return(match)
def fix(component):
    component = component.strip().upper()
    return component
def error_handle(parsed_string):
    new_dict = {}
    for thing in parsed_string:
        if thing[1] in new_dict.keys():
            a_list = [new_dict[thing[1]], thing[0]]
            new_dict[thing[1]] = max(a_list, key=len)
        else:
            new_dict[thing[1]] = thing[0]
    return(new_dict)
def clean_address_two(add_1):
    add_1 = fix(add_1)
    if add_1 == 'None':
        addr_1 = ''
    elif add_1 == 'NAN':
        addr_1 = ''
    else:
        addr_1 = ', ' + add_1
    return(addr_1)

def get_address_dict(address):
    try:
        address_dict = usaddress.tag(address)[0]
    except usaddress.RepeatedLabelError as e:
        print(e.original_string)
        address_dict = error_handle(e.parsed_string)
        print('')
    return address_dict
        
def parse_gov_address(moar):
    dict_list = []
    for row in moar.itertuples():
        addr_2 = clean_address_two(row.adr_ln_2)
        address = f'{fix(row.adr_ln_1)}{addr_2}, {fix(row.cty)}, {fix(row.st)}'
        address_dict = get_address_dict(address)
        address_dict['adrs_id'] = row.adrs_id
        address_dict['PHONE'] = row.phn_numbr
        address_dict['ZIPCODE'] = row.zip
        address_dict['ZIP'] = use.fix_zipcode(row.zip)
        dict_list.append(address_dict)
    parsed_df = pd.DataFrame(dict_list)
    parsed_df.dropna(how='all', axis=1, inplace=True)
    return (parsed_df)

def parse_bolo_address(moar):
    dict_list = []
    for row in moar.itertuples():
        addr_2 = clean_address_two(row.addr_line_3)
        address = f'{fix(row.addr_line_2)}{addr_2}, {fix(row.addr_city)}, {fix(row.addr_state)}'
        address_dict = get_address_dict(address)
        address_dict['comm_id'] = row.comm_id
        address_dict['ZIPCODE'] = row.addr_zip
        address_dict['ZIP'] = use.fix_zipcode(row.addr_zip)
        dict_list.append(address_dict)
    parsed_df = pd.DataFrame(dict_list)
    parsed_df.dropna(how='all', axis=1, inplace=True)
    return (parsed_df)

In [9]:
gov = gov.fillna('None')
gov_adds = gov.drop_duplicates('adrs_id')
gov_parsed = parse_gov_address(gov_adds)

CARR 129 KM 15, NONE, HATILLO, PR

2030 N ADAMS ST, 306 JOYCE A HIGASHI LCSW, ARLINGTON, VA

3330 NW 56TH ST, 608 WELL ROOTED HEATLH AND NUTRITION PLLC, OKLAHOMA CITY, OK

CARR 2 KM, 1 BO CANDELARIA, ARECIBO, PR

996 S MAIN ST, 102 SHANNON DEETS COUNSELING LLC, MEADVILLE, PA

CARR 2 KM, 2 PLAZA TAINA SUITE 2, ARECIBO, PR

1399 SCENIC N HWY 124, NONE, SNELLVILLE, GA

4343 S STATE RD, 7 SUITE 108, DAVIE, FL

10626 BUSINESS, 21 SUITE C, HILLSBORO, MO

110 HOPMEADOW ST, 2ND FLOOR SUITE 700, SIMSBURY, CT

128 W SPRUCE ST, 23 RAINBOWS END CONSULTING, SAULT SAINTE MARIE, MI

51 MENDEZ VIGO ST, CORNER OF PERAL ST, MAYAGUEZ, PR

2323 S 171ST ST, 100 JOHN W PFLUG MD PC, OMAHA, NE

CARR 363 KM 0, NONE, SABANA GRANDE, PR

1 SEARS DR, SUITE 403 4TH FLOOR, PARAMUS, NJ

CARR 111 KM 2, BO PALMAR, AGUADILLA, PR

4911 W ST JOE HWY 102, NONE, LANSING, MI

800 AUSTIN ST, 611 WEST TOWER, EVANSTON, IL

3441 24TH AVE NW, 105 R BRUCE PARKER MD, NORMAN, OK

1056 MUNOZ RIVERA AVE, FIRST FEDERAL SUITE 403, SAN J

CARR 110 KM, 2 EDIFICIO SAN JOSE SUITE 1 2 BO CEIBA BAJA, AGUADILLA, PR

1265 WAYNE AVE, 301 119 PROFESSIONAL CTR, INDIANA, PA

3 1 CARR PR 100 KM, NONE, CABO ROJO, PR

303 KINGS S HWY 1, NONE, CHERRY HILL, NJ

780 N 2860, SUITE 202, ST GEORGE, UT

1379 RT 28A UNIT, B1, CATAUMET, MA

SUITE A, SUITE 202, BAYAMON, PR

9868 S STATE RD, 7 SUITE 300, BOYNTON BEACH, FL

114 WALNUT HILL RD, WALNUT HILL SHOPPES UNIT 9, UNIONTOWN, PA

9149 SUGAR ESTATE, 206 PARAGON MEDICAL BUILDING, ST. THOMAS, VI

56244 PAPAGO TRAIL, SUITE 5 ROOM D, YUCCA VALLEY, CA

609 W LITTLETON BLVD, SUITE 210 DALE G RETZER DC, LITTLETON, CO

3450 ACWORTH DUE W RD NW, SUITE 320, KENNESAW, GA

50 LEANNI WAY, UNIT A3 AND A4, PALM COAST, FL

3209 S BROADWAY, 217 TEERA CHIROPRACTIC AND ACUPUNCTURE, EDMOND, OK

96 E MAIN ST, 2ND FLOOR SUITE 1, EAST ISLIP, NY

2151 S ALT, A1A SUITE 950, JUPITER, FL

1245 WILSHIRE BLVD, SUITE 680 S TOWER, LOS ANGELES, CA

URB BAIROA ST 27, 1 LOCAL 3, CAGUAS, PR

CARR 2 KM 414, BO CAIMITAL BAJO, 

77 NEWARK AVE, 2ND FL UNIT 3, BELLEVILLE, NJ

2851 S AVE B, SUITE 2401, YUMA, AZ

CARR 3 HM, 9 EDIF EAST MEDICAL PROFESSIONAL CENTER, CANOVANAS, PR

1845 CARR, 2 SUITE 809 BAYAMON MED PLAZA, BAYAMON, PR

5635 S WATERBURY WAY C, SUITE 202, SALT LAKE CITY, UT

222 PERRY HWY, PULASKI PROFESSIONAL BLDG B, HAWKINSVILLE, GA

888 E, 163 SUITE 3, BRONX, NY

CALLE 55 BLQ 11 NUM, 6 ROYAL TOWN, BAYAMON, PR

1265 WAYNE AVE, 119 PROFESSIONAL CENTER SUITE 203, INDIANA, PA

CARR 2 KM, 3 1338 SUITE 2, ARECIBO, PR

59 OLD RD TO 9 ACRE COR, SUITE 2, CONCORD, MA

57 RT, 6A UNIT 1B, ORLEANS, MA

29 WASHINGTON ST, ASHFORD MEDICAL CENTER 209, SAN JUAN, PR

CARR 102 ESQ, 16 URB BORINQUEN, CABO ROJO, PR

2365 GAUSE E BLVD E, NONE, SLIDELL, LA

1710 E SAUNDERS ST B, SUITE 350, LAREDO, TX

7100 W CAMINO REAL, SUITE 302 OFFICES 9 AND 10, BOCA RATON, FL

68 CALLE SANTA CRUZ, TORRE SAN PABLO SUITE 703, BAYAMON, PR

21910 S CONDUIT AVE, LOWER LEVEL 1, SPRINGFIELD GARDENS, NY

7200 MINNETONKA BLVD, NONE, ST LOUIS PA

210 CENTRAL EXPRESSWAY S, 36 DR AMY WOOD DC, ALLEN, TX

100 LUIS MUNOZ MARIN AVE HIMA CA, 1ST, CAGUAS, PR

550 CASCADE W PKWY SE, NONE, GRAND RAPIDS, MI

1833 E 13TH ST, SUITE CA, BROOKLYN, NY

255 W SPRING VALLEY AVE, SECOND FLOOR SUITE 200, MAYWOOD, NJ

505 N RIDGEWAY DR, 195 NAOMI R HARMAN MD, CLEBURNE, TX

HOSPITAL WILMA N VAZQUEZ, CARR 2 KM 39.5 SUITE 105, VEGA BAJA, PR

1711 W TEMPLE ST, DEPARTMENT OF RADIOLOGY, LOS ANGELES, CA

3100 S NATIONAL AVE, 100 FAMILY BACK AND NECK CARE CENTRE, SPRINGFIELD, MO

90 MT S HWY 91, SUITE 2, DILLON, MT

1800 COOPER POINT SW RD, 24B, OLYMPIA, WA

4081 E OLYMPIC BLVD, DEPARTMENT OF RADIOLOGY, LOS ANGELES, CA

21 STATE ROUTE 3305 S, NONE, EDDYVILLE, KY

2851 S AVE B, SUITE 3001, YUMA, AZ

115 POINTER W TRL B, NONE, VAN BUREN, AR

CARR 401 KM, 5 BIO PLAYA, ANASCO, PR

1 S 376 SUMMIT T C, UNIT 4BC, OAKBROOK TERR, IL

CARR 416 KM 8, NONE, AGUADA, PR

55 N DR BASORA ST, MEDICO IV SUITE 103, MAYAGUEZ, PR

514 LAFAYETTE RD ROUTE 15 E, HERITAGE HEALTH A

2221 IRON WOOD CTR N DR, NONE, COEUR D ALENE, ID

1495 W ST RD, 434 SUITE 109, LONGWOOD, FL

10110 DON S POWERS DR, 201A SUITE 201A, MUNSTER, IN

3970 SO 700 E, 14 BRYANT J BROWN MDPC, SALT LAKE CITY, UT

5656 EDWARDS RANCH RD, 202 MATTHEW H STEELE MD COSMETIC AND RECONSTRUCTIVE PL, FORT WORTH, TX

CARR 111 KM 1, FERNANDO L. RIBAS DOMINICCI, UTUADO, PR

1057 BROAD ST, SUMTER MALL BOX 1, SUMTER, SC

365 COUNTY RD, 39A UNIT 9, SOUTHAMPTON, NY

CARR 183 R 917 KM 1, SECTOR EULOGIO REYES, LAS PIEDRAS, PR

7000 N MOPAC EXPRESSWAY, 2127 PLAZA 7000, AUSTIN, TX

5 WASHINGTON ST, 300 PMB 65, VALPARAISO, IN

1845 CARR, 2 SUITE 506, BAYAMON, PR

107 GONZALEZ GIUSTI AVE, CAPARRA GALLERY BLDG SUITE 305, GUAYNABO, PR

1617 NORMANDY COURT, 100 SUITE 100, LINCOLN, NE

333 E CITY AVE, IL SUITE 35, BALA CYNWYD, PA

41 E 11 ST, 4TH FLOOR 50, NEW YORK, NY

138 W 25TH ST, SUITE 802 ROOM B2, NEW YORK, NY

CARR 2 KM, 4 PLAZA CONSTANCIA SUITE 103 B, HORMIGUEROS, PR

CARR 474 KM 2, NONE, ISABELA, PR

CARR 3 KM,

...

9501 BAPTIST HEALTH DR MEDICAL TOWER, 940 ALLEVIANT HLTH CTRS, LITTLE ROCK, AR

845 FM 1960 W, 104 GENESIS MEDICAL GROUP, HOUSTON, TX

837 FM 1960 W RD, 107 GENESIS MEDICAL GROUP, HOUSTON, TX

765 N KELLOGG ST, 203 RENALCARE ASSOCIATES SC, GALESBURG, IL

434 PEPPERS FERRY NW RD, NONE, CHRISTIANSBURG, VA

5625 EIGER RD, 220 TEXAS HEART AND VASCULAR, AUSTIN, TX

3101 HWY 71 E, SUITE 201 TX HEART AND VASCULAR, BASTROP, TX

1253 N VON MINDEN ST, TEXAS HEART AND VASCULAR, LA GRANGE, TX

3747 WILLIAM PENN HWY, NOVACARE REHABILITATION 50231, MONROEVILLE, PA

495 E WATERFRONT DR, 240 NOVACARE REHABILITATION 50248, HOMESTEAD, PA

321 N FURNACE ST, NOVACARE REHABILITATION 50208, BIRDSBORO, PA

148 E MAIN ST, NOVACARE REHABILITATION 50250, CARNEGIE, PA

2557 W STATE ST, NOVACARE REHABILITATION 50220, NEW CASTLE, PA

210 S PERRY ST A, NOVACARE REHABILITAITON 50204, TITUSVILLE, PA

300 N POINTE CIR, NOVACARE REHABILITAITON 50234, SEVEN FIELDS, PA

5996 STEUBENVILLE PIKE, NONE, MC KEES ROCKS, PA

17

14714 PARK AVE EXT, MEADVILLE REHAB AND NURSING CTR, MEADVILLE, PA

2000 WASHINGTON ST, MOB WHITE 544, NEWTON, MA

60 E END AVE, PRIVATE ENTRANCE, NEW YORK, NY

5317 E 16TH ST, JANE PAULEY CHC AT 16TH STREET INC, INDIANAPOLIS, IN

805 W CEDAR ST, ST MARYS OF STANDISH, STANDISH, MI

163 ROUTE 130, NONE, BORDENTOWN, NJ

ATRIA - W 86TH ST, 333 WEST 86TH ST., NEW YORK, NY

6001 NW 139TH ST, NEUROPATHY TREATMENT CLINIC OF OKLA, OKLAHOMA CITY, OK

500 W BROADWAY, BROADWAY BLDG 4TH FLOOR, MISSOULA, MT

2401 W TURNER RD, 250 CENTRAL VALLEY PHY THER, LODI, CA

15435 W 134TH PL, 103 OHFM BLACKFOOT, OLATHE, KS

801 N MUR LEN RD, 201 OHFM MURLEN, OLATHE, KS

20375 W 151ST ST, 151 OHFM OLATHE MEDICAL PARK, OLATHE, KS

105 E 9TH ST, IOWA RIVER LANDING UNIVERSITY OF IOWA HEALTHCARE, CORALVILLE, IA

411 10TH ST SE, 150 UNIVERSITY OF IA FAM CHILD HOSP PEDS CEDAR RAPIDS, CEDAR RAPIDS, IA

50 NEWTON RD, UNIVERSITY OF IOWA COLLEGE OF NURSING, IOWA CITY, IA

425 COLLEGE OF NURSING BUILDING 50 NEWTON RD, UN

1518 RANCH RD 620, SUITE 100, LAKEWAY, TX

3720 N ANKENY BLVD, 103 FOOT AND ANKLE CENTER OF IOWA, ANKENY, IA

26908 INDEPENDENCE WAY, 100 LERAY CMNS, EVANS MILLS, NY

1700 UNIVERSITY DR E ENTRANCE 16, CARE CLINIC COLLEGE STATION UNIVERSITY DRIVE, COLLEGE STATION, TX

1340 WONDER WORLD DR, 2300 BAYLOR SCOTT AND WHITE CLINIC SAN M, SAN MARCOS, TX

1800 S A W GRIMES BLVD, BAYLOR SCOTT AND WHITE CLINIC ROUND, ROUND ROCK, TX

1700 UNIVERSITY DR E ENTRANCE 16, NONE, COLLEGE STATION, TX

2301 N UNIVERSITY DR, SUITE 211 2ND FLOOR, PEMBROKE PINES, FL

3377 S STATE RD, 7 SUITE 100, WELLINGTON, FL

1609 W 40TH AVE, 401 GI ASSOCIATES SUITE 401, PINE BLUFF, AR

1609 W 40TH AVE, 201 OBGYN ASSOCIATES OF S ARK, PINE BLUFF, AR

1609 W 40TH AVE, 204 OBGYN ASSOCIATES OF S ARK, PINE BLUFF, AR

1609 W 40TH AVE, 402 OBGYN ASSOCIATES OF S ARK, PINE BLUFF, AR

41 WACONAH ST, UROLOGICAL SERVICES OF BERKSHIRE MEDICAL CENTER, PITTSFIELD, MA

100 HOSPITAL DR, SOUTH WESTERN VERMONT MEDICAL CENTER, BENNINGTON, VT



5046 HWY 17 S BYP 105, NONE, MYRTLE BEACH, SC

20871 IH, 35 SUITE 100, KYLE, TX

3000 SW 148TH AVE, 1147 MIRAMAR OB/GYN LLC, MIRAMAR, FL

17900 NW 5TH ST, 204 ADULT AND PEDIATRIC DERMATOLOGY, PEMBROKE PINES, FL

1200 N UNIVERSITY DR, 1 SOTL OB GYN SERV, PLANTATION, FL

2300 N COMMERCE PKWY, 113 VIP PEDIATRIS LLC, WESTON, FL

7300 SW 62ND PLACE 3RD FLOOR, SOUTH MIAMI OB GYN ASSOCIATES LLC, CORAL GABLES, FL

601 E DIXIE AVE, 401 LAKE OB/GYN ASSOCIATES OF MID FLORI, LEESBURG, FL

8720 N KENDALL DR, 115 LIEVANO'S OB GYN LLC, MIAMI, FL

8740 N KENDALL DR, 215 ALLERG AND IMMUNOLOGY CENTER, MIAMI, FL

3319 S STATE RD, 7 SUITE 110, WELLINGTON, FL

603 N FLAMINGO RD, 361 GEMINI OBGYN LLC, PEMBROKE PINES, FL

480 WARTAHOO LN, COW CREEK HLTH AND WELLNESS CTR, CANYONVILLE, OR

5046 HWY 17 S BYP 100, NONE, MYRTLE BEACH, SC

CARR NUM 21 BLOQUE, 5 LAS LOMAS RIO PIEDRAS, SAN JUAN, PR

1155 PLEASANT VALLEY WAY, DAUGHTERS OF ISRAEL, WEST ORANGE, NJ

1000 18TH ST NW, 2ND AND 3RD FLOORS, MANDAN, ND

620 W

142 WALLACE AVE, 201 GATEWAY MEDICAL ASSOCIATE PC, DOWNINGTOWN, PA

219 S WASHINGTON ST, UNIVERSITY OF MARYLAND MEDICAL CENTER AT EASTON, EASTON, MD

3347 STATE RD, 7 SUITE 200, WELLINGTON, FL

7915 US HWY 301 N 107, DERMATOLOGY ASSOCIATES OF SARASTOA, ELLENTON, FL

221 E 29TH ST, 102 UCHMG IM/OCCMED/DM/ENDO ORCHARDS, LOVELAND, CO

175 S UNION BLVD, 315 UCHMG OCCUPATIONAL HEALTH UNION, COLORADO SPRINGS, CO

1725 E BOULDER ST, 101 UCHMG NEUROSCIENCES COLORADO SPRINGS, COLORADO SPRINGS, CO

601 S MAIN ST, PRIMARY CARE KEN PRATT BLVD, LONGMONT, CO

525 BOB PETERS GRV, 202 UCHMG HEMATOLOGY/ONCOLOGY, COLORADO SPRINGS, CO

2450 S PEORIA, 245 UCHMG VIRTUAL VISIT, AURORA, CO

CARR 2 KM, 628 SECTOR CANDELARIA, ARECIBO, PR

CARR 2 KM, 8 SECTOR CANDELARIA, ARECIBO, PR

11361 N 99TH AVE, 601 WEST VALLEY, PEORIA, AZ

605 JEFFERSON DAVIS HWY 202, NONE, FREDERICKSBURG, VA

401 E VAUGHN AVE, NORTHERN LA MED CTR, RUSTON, LA

609 W MEMORIAL RD, FOOT AND ANKLE CENTER OF OKLAHOMA, OKLAHOMA CITY, OK

8146 

In [10]:
bolos = bolos.fillna('None')
bolo_parsed = parse_bolo_address(bolos)

2835 E HIGHWAY 76 STE 5, STE 100C, MULLINS, SC

PO BOX 973, BOX 800, BENNETTSVILLE, SC

200 QUEENS RD STE 400, STE 400, CHARLOTTE, NC

19 COLONIAL ST, ANESTHESIA ASSOCIATES P A, CHARLESTON, SC

180 WINGO WAY, DEPT RADIOLOGY, MT PLEASANT, SC

PO BOX 70, REN 11ST FLOOR, SANDY SPRINGS, SC

1301 TAYLOR ST STE 6J, STE 300, COLUMBIA, SC

2650 MIDDLE ST, DEPARTMENT OF RADIOLOGY, SULLIVANS IS, SC

3492 CHERRYWOOD RD, MALL A SUUITE 230, FLORENCE, SC

1 DOCTORS DR, 200 PATEWOOD DR, GREENVILLE, SC

404 WESTWOOD AVE STE 205, MARTINSBURG VA MEDICAL CENTER, HIGH POINT, NC

6691 E POWERS AVE, CHILDREN'S HOSPITAL OF COLO DEPT OF NEU, GREENWOOD VLG, CO

404 E CALHOUN ST, 420 THOMSON CIR, ANDERSON, SC

2605 WATERSTONE DR, 3700 WASINGTON AVE, EVANSVILLE, IN

2728 SUNSET BLVD STE 306, STE 306, WEST COLUMBIA, SC

2728 SUNSET BLVD STE 201, STE 201, WEST COLUMBIA, SC

8401 DATAPOINT DR STE 600, STE 110, SAN ANTONIO, TX

241 LANDS END DR, 512 W BEACH CT, CHARLESTON, SC

97 PONSBURY RD, DEPT OF RADIOLOGY, MT P

2220 RIVERSIDE AVE, MAIL STOP 31700A, MINNEAPOLIS, MN

0720 SW GAINES ST UNIT 217, STE 100, PORTLAND, OR

1515 CHAIN BRIDGE RD STE G, STE 1527, MC LEAN, VA

MC 158, 47 NEW SCOTLAND AVENUE, ALBANY NY 12, NY

2201 MURPHY AVE STE 210, STE 210, NASHVILLE, TN

919 JASMINE ST STE 100, STE G104, DENVER, CO

1161 21ST AVE S, # D5237 MED CTR N DEPT VS, NASHVILLE, TN

4545 CORDATA PKWY STE 1E, PEDIATRICS GROUP 1E, BELLINGHAM, WA

725 10TH AVE SW, 200 IST ST SW, ROCHESTER, MN

325 9TH AVE, 1959 NE PACIFIC ST, SEATTLE, WA

30 PROSPECT AVE, NEW JERSEY WOMEN'S WELLNESS CENTER, HACKENSACK, NJ

PO BOX 4000, TENNESSEE DEPARTMENT OF HEALTH, MOUNTAIN HOME, TN

PO BOX 1201, LIMITED TO OFFICIAL GOVERNMENT DUTIES ON, PINE RIDGE, SD

995 POTRERO AVE RM 314, SF GEN HOSP WARD 8B BLD 80, SAN FRANCISCO, CA

1600 SW ARCHER RD, LIMITED TO OFFICIAL GOVERNMENT DUTIES ON, GAINESVILLE, FL

55 COMMODORE PKWY, 738 LIBRARY RD, ROCHESTER, NY

PO BOX 245057, P O BOX 245057, TUCSON, AZ

310 25TH AVE N STE 105, NASHVILLE SUI

1616 MASSEY POINTE LN, MAIL STOP 810, MEMPHIS, TN

1909 MALLORY LN STE 301, STE 301, FRANKLIN, TN

8014 BURNETT WOMACK BLDG, UNIVERSITY OF NORTH CAROLINA, CHAPEL HILL, NC

4342 OAKTON DR, MEDICAL CENTER BLVD, HIGH POINT, NC

10134 COLVIN RUN RD STE D, STE 225, GREAT FALLS, VA

334 ANGELUS ST, 5TH FLOOR ADAMS BLDG, MEMPHIS, TN

PO BOX 3627, PHYSICIAN SERVICES OF CLEVELAND PC, CLEVELAND, TN

6026 SIX FORKS RD STE 100, 721 TUCKER STREET, DURHAM, NC

171 ASHLEY AVE, MEDICAL UNIVERSITY OF SOUTH CAROLINA, CHARLESTON, SC

6215 HUMPHREYS BLVD STE 500, STE 500, MEMPHIS, TN

830 HARRISON AVE, MOAKLEY 3RD FLOOR, BOSTON, MA

2001 HIGHLAND AVE, GENERATIONS OB GYN, P.C., KNOXVILLE, TN

111 W MANOR ST, SHRINERS HOSP CHILD/N CA, ALTADENA, CA

300 20TH AVE N STE 403, STE 430, NASHVILLE, TN

4958 COQUINA KEY DR SE, UNIT100, ST PETERSBURG, FL

321 W MOUNT AIRY AVE, CHOP SUITE 301, PHILADELPHIA, PA

51 N DUNLAP ST, UNIVERSITY OF TENNESSEE, MEMPHIS, TN

8456 GLENBRAE CV, V A MEDICAL CENTER 614/116A, GERMAN

13601 PRESTON RD STE 900W, STE 1000W, DALLAS, TX

1901 MONTEREY HWY STE 10, STE 200, SAN JOSE, CA

3072 ACECA DR, ADMINSTRATION 4TH FLOOR, LOS ALAMITOS, CA

7121 SPID DR STE 300, STE 300, CORP CHRISTI, TX

11410 COUNTY ROAD 311, 11410 COUNTY ROAD 311, CALDWELL, TX

3000 N IH 35 STE 770, STE 405, AUSTIN, TX

811 HULEN DR, 1216 MORGAN MEDICAL UNIT, COLUMBIA, MO

2700 E 29TH ST STE 105, STE 105, BRYAN, TX

1481 BUTLER DR, 120 E BEAUREGARD, SAN ANGELO, TX

13601 PRESTON RD STE 900W, STE 1000W, DALLAS, TX

3705 MEDICAL PKWY STE 570, STE 570, AUSTIN, TX

6621 FANNIN ST, DEPT PATH MSC 1-2261, HOUSTON, TX

4375 BOOTH CALLOWAY RD, STE 307, N RICHLND HLS, TX

6500 N MO PAC EXPY STE II-2207, STE 350, AUSTIN, TX

1301 BARBARA JORDAN BLVD STE 300, STE 1300, AUSTIN, TX

650 BELVIDERE ST, LIMITED TO OFFICIAL GOVERNMENT DUTIES ON, EL PASO, TX

755 E MCDOWELL RD, NEUROLOGY DEPARTMENT 3RD FLOOR,, PHOENIX, AZ

6365 E MISSION BLVD, 55 W SUNBRIDGE, FAYETTEVILLE, AR

534 BILTMORE AVE, 534 BILTMORE AVE, ASHE

PO BOX 12065, P O BOX 12065, NEW BERN, NC

414 CASCADA WAY, 223 N FIRST AVE STE 201, LOS ANGELES, CA

4716 ALLIANCE BLVD STE 200, STE 100, PLANO, TX

1709 DRYDEN RD STE 1617, SCOTT DEPT OF UROLOGY-BAYLOR FACULTY CTR, HOUSTON, TX

7707 FANNIN ST STE 100, STE 107, HOUSTON, TX

101 LOMBARD ST APT 709W, STE 104, SAN FRANCISCO, CA

7737 SOUTHWEST FWY STE 201, STE 302, HOUSTON, TX

6560 FANNIN ST STE 1700, STE C143, HOUSTON, TX

1450 DANDIE WAY, 841 MALCOLM BLVD, ESTES PARK, CO

400 PARNASSUS AVE, 1 GUSTAVE L LEVY PL, SAN FRANCISCO, CA

901 W 38TH ST STE 200, STE 200, AUSTIN, TX

50 N MEDICAL DR, 2543 LUPINE LN, SALT LAKE CTY, UT

300 PASTEUR DR, EAST VALLEY MEDICAL CLINIC, STANFORD, CA

3705 MEDICAL PKWY STE 250, STE 102, AUSTIN, TX

17 VALERIA CIR, WHITE PLAINS HOSPITAL DEPARTMENT OF BEHA, NORTH SALEM, NY

3175 ALLERTON LAKE DR, 1 MEDICAL CENTER BOULEVARD, WINSTON SALEM, NC

4015 INTERSTATE 45 N STE 230-1, STE 200, CONROE, TX

1551 BISHOP ST STE 510, STE 230, SN LUIS OBISP, CA

1135 S SUNS

...

7138 S 2000 E STE 106, STE 106, SALT LAKE CTY, UT

1 COUNTRY CLUB PL, 2ND FLOOR WHITE BUILDING, S ABINGTN TWP, PA

3001 GREEN BAY RD, CAPT JAMES A LOVELL FHCC, NORTH CHICAGO, IL

4175 S ALAMO AVE, 355TH MEDICAL GROUP, DM AFB, AZ

124 MILL BROOK LN, 3910 BLDG 2ND FL, MEDIA, PA

201 UNIVERSITY OAKS STE 1260, STE 201, ROUND ROCK, TX

15 S 8TH ST STE 200, STE 200, INDIANA, PA

901 23RD ST NW, DEPT OF RADIOLOGY NW, WASHINGTON, DC

2201 MURPHY AVE STE 207, STE 207, NASHVILLE, TN

700 WEST AVE S, FRANCISCAN SKEMP HLTHCARE, LA CROSSE, WI

407 HIGHGATE DR, NEW LIFE CARDIOVASCULAR CA, AMBLER, PA

2412 NAUDAIN ST, CHILDREN'S HOSPITAL OF PHILADELPHIA - NE, PHILADELPHIA, PA

7408 MEADOW LN, 30 CONVENT DR, CHEVY CHASE, MD

526 SCHOOL LN, DIVISION OF CRITICAL CARE, SWARTHMORE, PA

2217 GREEN ST APT 1, STE 131, PHILADELPHIA, PA

36 CATHLEEN DR, PCAM / TRC 4 WEST, RICHBORO, PA

1115 MORRIS AVE, PENN CARDIOLOGY HUP CEDAR AVE, BRYN MAWR, PA

1984 PEACHTREE RD NW, CONSULTANTS LLCSUITE 515, ATLANTA, GA

28

51 E 25TH ST, FIFTH FLOOR STE 9, NEW YORK, NY

1260 E WOODLAND AVE STE 20, PRACTICE R, SPRINGFIELD, PA

401 E CHESTNUT ST UNIT 170, UNIT 170, LOUISVILLE, KY

419 N STRATFORD RD, MEDICAL CENTER BLVD, WINSTON SALEM, NC

1501 NE MEDICAL CENTER DR, 501 NE MEDICAL CENTRE DRIV, BEND, OR

12 CLEAR BRK, 300 68TH ST SE, FARMINGTON, CT

615 OVERLOOK RD N, UNIVERSITY MEDICAL CTR, TUSCALOOSA, AL

109 BREELEY BLVD, BUILDING 6 ROM 1B25, MELVILLE, NY

281 CASSIDY AVE, 900 S LIMESTONE ST, LEXINGTON, KY

1090 VICTOR LN, HCC II STE 2408, BRYN MAWR, PA

550 1ST AVE HCC3C, STE 8R, NEW YORK, NY

200 NORTH ST STE 101, STE 303, GENEVA, NY

1636 CHELSEA RD, LOS ANGELES CTY MED CTR, PLS VRDS EST, CA

3300 WEBSTER ST STE 1106, STE B1, OAKLAND, CA

750 WELCH RD STE 317, DIVISION OF CHILD NEUROLOGY, PALO ALTO, CA

10 EASTLAND AVE, LIMITED TO OFFICIAL GOVERNMENT DUTIES ON, ROCHESTER, NY

2818 CHERRYSTONE PL, CHEYENNE VA MEDICAL CENTER, FORT COLLINS, CO

307 S EVERGREEN AVE, 100 TOWNSEND AVE, WOODBURY, NJ

800 TREN

PO BOX 1917, MENDEZ VIGO ST 61 EAST, MAYAGUEZ, PR

151 MEADOWCREST ST STE F, STE F, GRETNA, LA

PO BOX 360314, CALLE 22 BLOQUE NUMERO 10, SAN JUAN, PR

917 AVE TITO CASTRO, TORRE MEDICA SAN LUCAS SUITE 523, PONCE, PR

193 DORADO BCH E, 402 CALLE SANTA CRUZ 66, BAYAMON, PR

400 AVE DOMENECH STE 506, STE 506, SAN JUAN, PR

1725 CALLE LILAS, 172 OFICINA 110, CAGUAS, PR

1785 CARR 21, 21 SUITE 311, SAN JUAN, PR

619 19TH ST S, 525 NHB, BIRMINGHAM, AL

5641 NE 21ST RD, DEPARTMENT OF RADIOLOGY, FT LAUDERDALE, FL

66 CALLE SANTA CRUZ, SAN PABLO INSTITUTO SUITE 409, BAYAMON, PR

PO BOX 13030, P O BOX 13030, ALEXANDRIA, LA

2617 NE 23RD ST, ACC E RM #352 (D48), FT LAUDERDALE, FL

7777 SOUTHWEST FWY STE 900, STE 900, HOUSTON, TX

1434 E SONTERRA BLVD STE 210, STE 217, SAN ANTONIO, TX

3798 JANES RD STE 18, 119 FONT MARTELO ST, ARCATA, CA

369 CALLE DE DIEGO STE 504, 369 SUITE 504 TORRE SAN FRANCISCO, SAN JUAN, PR

1307 FEDERAL ST STE 301, STE 301, PITTSBURGH, PA

3661 S MIAMI AVE STE 801, STE 20

ESQ PERAL ST, CORNER OF PERAL ST, MAYAGUEZ, PR

1821 CITY PARK BLVD, 1337 CENTRE CT, ALEXANDRIA, LA

CARR. 639 KM4.8, CARR 639 KM 4 8 BO SABANA HOYOS, ARECIBO PR, PR

3802 CARAVELLE PKWY APT 3411, STE 101-C, CORP CHRISTI, TX

2682 TRANQUILLA WAY, WOMENS SPECIALISTS OF NORTH GEORGIA LLC, DULUTH, GA

212 S FLORIDA ST, ORLANDO VA MEDICAL CENTER, BUSHNELL, FL

101 AVE SAN PATRICIO STE 1050, 3 R.D.C.M. GRP MED INTRNA HAC, CAROLINA, PR

13 CARR 693 BO BRENAS, PLAZA DEL MAR SHOPPONG CENTER 201 A, VEGA ALTA, PR

4582 CAMPOBELLO ST, MAIL STOP #52, SAN DIEGO, CA

2521 13TH ST STE D, SUITE B, SAINT CLOUD, FL

SUITE 210, SUITE 210 BO RINCON SECTOR LOMA CARR 14, CAYEY, PR

DOMENECH 500 ST 401 B, STE 304, HATO REY, PR

U3-4 CARR 21, SUITE 21, SAN JUAN, PR

S-C 1353 CARR 19 GARDENS H, SUITE 21, TRUJILLO ALTO, PR

19 RES BONNEVILLE HTS APT A11, DEGETAU A11, CAGUAS, PR

PO BOX 2152, BOX 2152, JUNCOS, PR

1758 CALLE AFRODITA, AFRODITA 1758 VENUS GARDENS, RIO PIEDRAS, PR

2225 PONCE BYP, PARA BLDG SUITE 

1514 JEFFERSON HWY, DEPT OF RADIOLOGY SPRINGS, NEW ORLEANS, LA

9 MILLS AVE, 3911 S HYWEY 14, GREENVILLE, SC

1000 JOHNSON FY RD NE # PTH, STE 178, ATLANTA, GA

1867 ACUBA LN NE, DEPT OF EMERGENCY MEDICINE, ATLANTA, GA

800 MONTCLAIR RD, DEPARTMENT OF PATHOLOGY, BIRMINGHAM, AL

1410 BRENTWOOD DR, 5 RICHLAND MEDICAL PARK DR, COLUMBIA, SC

364 WINTER WALK DR, 8901 WISCONSIN AVE, GAITHERSBURG, MD

FIRST AVE & 27TH ST, BELLEVUE HOSP CTR 2N69, NEW YORK, NY

4913 HIDEAWAY PT, 606 BLACK RIVER RD, HOLLYWOOD, SC

127 BRIAN DR, NORTH SPARTANBURG FIRE & E, SPARTANBURG, SC



In [11]:
gov_all_parsed = pd.merge(gov, gov_parsed, on='adrs_id')
bolos_all_parsed = pd.merge(bolos, bolo_parsed, on='comm_id').drop_duplicates('ME')

In [12]:
just_a_test = pd.merge(bolos_all_parsed, gov_all_parsed, on='ME', suffixes = ['_BOLO','_GOV'])
just_a_test = just_a_test.fillna('None')

In [13]:
dicts =[]
for row in just_a_test.itertuples():
    MATCH = False
    if row.addr_state == row.st:
        if is_a_match(row.StreetName_GOV, row.StreetName_BOLO,80):
            MATCH = True
        elif row.ZIP_GOV == row.ZIP_BOLO and is_a_match(row.adr_ln_1, row.addr_line_2, 75):
            MATCH = True
        if MATCH == True:
            score = fuzz.ratio(row.adr_ln_1, row.addr_line_2)
            print(f'{row.adr_ln_1} is {row.addr_line_2}')
            new_dict = {
                'ME': row.ME,
                'adrs_id': row.adrs_id,
                'comm_id': row.comm_id,
                'GOV_ADDR': row.adr_ln_1,
                'BOLO_ADDR': row.addr_line_2,
                'GOV_ZIP': row.ZIP_GOV,
                'BOLO_ZIP':row.ZIP_BOLO,
                'SCORE': score,
                'PHONE': row.PHONE
                }
            dicts.append(new_dict)

2525 COURT DR is 2525 COURT DR
2545 COURT DR is 2525 COURT DR
2511 COURT DR is 2525 COURT DR
2525 COURT DR is 2525 COURT DR
8 RICHLAND MEDICAL PARK DR is 8 RICHLAND MEDICAL PARK DR STE 300
131 PROVIDENCE RD is 200 PROVIDENCE RD
131 PROVIDENCE RD is 200 PROVIDENCE RD
131 PROVIDENCE RD is 200 PROVIDENCE RD
131 PROVIDENCE RD is 200 PROVIDENCE RD
131 PROVIDENCE RD is 200 PROVIDENCE RD
131 PROVIDENCE RD is 200 PROVIDENCE RD
2739 LAUREL ST is 2739 LAUREL ST
4220 HARDING PIKE is 4220 HARDING PIKE
701 CASHUA FERRY RD is PO BOX 811
1721 EBENEZER RD is 1721-05 EBENEZER RD STE 145
360 N IRBY ST is 360 N IRBY ST
619 19TH ST S is 619 19TH ST S
619 19TH ST S is 619 19TH ST S
619 19TH ST S is 619 19TH ST S
619 19TH ST S is 619 19TH ST S
619 19TH ST S is 619 19TH ST S
1255 VISCAYA PKWY is 1255 VISCAYA PKWY
880 SEVEN HILLS DR is 880 SEVEN HILLS DR
1900 HARRISON AVE is 1900 HARRISON AVE
180 WINGO WAY is 180 WINGO WAY
1 CANNON DR is 1 CANNON DR
808 FARRAR DR is 808 FARRAR DR
347 FOLLY RD is 347 FOLLY RD


200 1ST ST SW is 200 1ST ST SW
200 1ST ST SW is 200 1ST ST SW
200 1ST ST SW is 200 1ST ST SW
200 1ST ST SW is 200 1ST ST SW
200 1ST ST SW is 200 1ST ST SW
200 1ST ST SW is 200 1ST ST SW
200 1ST ST SW is 200 1ST ST SW
200 1ST ST SW is 200 1ST ST SW
200 1ST ST SW is 200 1ST ST SW
200 1ST ST SW is 200 1ST ST SW
1960 N OGDEN ST is 1960 N OGDEN ST STE 340
1325 S CLIFF AVE is 1417 S CLIFF AVE
1417 S CLIFF AVE is 1417 S CLIFF AVE
6151 LAKESIDE DR is 6151 LAKESIDE DR
2450 RIVERSIDE AVE is 2450 RIVERSIDE AVE
102 MCNEEL LN is 102 MCNEEL LN STE 1
730 WILSON ST is 730 WILSON ST
10350 E DAKOTA AVE is 10350 E DAKOTA AVE
10350 E DAKOTA AVENUE B is 10350 E DAKOTA AVE
10350 E DAKOTA AVENUE C is 10350 E DAKOTA AVE
10350 E DAKOTA AVE is 10350 E DAKOTA AVE
10350 E DAKOTA AVENUE B is 10350 E DAKOTA AVE
10350 E DAKOTA AVENUE C is 10350 E DAKOTA AVE
10350 E DAKOTA AVE is 10350 E DAKOTA AVE
10350 E DAKOTA AVENUE B is 10350 E DAKOTA AVE
10350 E DAKOTA AVENUE C is 10350 E DAKOTA AVE
10350 E DAKOTA AVE is 10350 

1101 BEACON ST is 1101 BEACON ST 6W
1611 NW 12 AVE is 1611 NW 12TH AVE
1611 NW 12TH AVE ACC E is 1611 NW 12TH AVE
1611 NW 12TH AVE ACC W is 1611 NW 12TH AVE
1611 NW 12TH AVE N WING is 1611 NW 12TH AVE
1611 NW 12TH AVE ACC WEST is 1611 NW 12TH AVE
1611 NW 12TH AVE JMH is 1611 NW 12TH AVE
1611 NW 12TH AVE 2ND FL is 1611 NW 12TH AVE
1611 NW 12TH AVE FL is 1611 NW 12TH AVE
1611 NW 12TH AVE DTC 1ST FLR is 1611 NW 12TH AVE
1611 NW 12TH AVE 2ND FLR is 1611 NW 12TH AVE
1611 NW 12TH AVE 5TH FLOOR is 1611 NW 12TH AVE
1601 NW 12TH AVE 1ST FLR is 1611 NW 12TH AVE
1611 NW 12TH AVE JMH 5TH FL is 1611 NW 12TH AVE
1611 NW 12TH AVE-NICU is 1611 NW 12TH AVE
1611 NW 12TH AVE E is 1611 NW 12TH AVE
1601 NW 12TH AVE is 1611 NW 12TH AVE
1601 NW 12TH AVENUE 5065 / 5TH FLOOR is 1611 NW 12TH AVE
1611 NW 12TH is 1611 NW 12TH AVE
1611 NW 12TH AVE ACC E 2ND FLR is 1611 NW 12TH AVE
1601 NW 12TH AVE ROOM is 1611 NW 12TH AVE

89
------------------------------------
1611 NW 12 TH AVE is 1611 NW 12TH AVE
1601 NW 12TH A

2305 S HWY 65 is 2305 S HIGHWAY 65
2305S HWY 65 is 2305 S HIGHWAY 65
11 UPPER RIVERDALE RD is 11 UPPER RIVERDALE RD SW
MEDICAL CTR BLVD is 4342 OAKTON DR
7901 FARROW RD is 7901 FARROW RD
1235 E CHEROKEE ST is 1235 E CHEROKEE ST
1235 E CHEROKEE ST RM is 1235 E CHEROKEE ST
171 ASHLEY AVE is 171 ASHLEY AVE
1114 W MADISON AVE NW is PO BOX 843
1296 SIMS ST is 1296 SIMS ST
1000 N LEE AVE is 1000 N LEE AVE
1758 PARK PL is 1758 PARK PL STE 201
6215 HUMPHREYS is 6215 HUMPHREYS BLVD STE 500
6408 PAPERMILL DR is 6408 PAPERMILL DR
1924 ALCOA HWY is 1924 ALCOA HWY

81
------------------------------------
1928 ALCOA HWY 127 is 1924 ALCOA HWY
1924 ALCOA HWY U106 is 1924 ALCOA HWY
1930 ALCOA HWY is 1924 ALCOA HWY
1605 NASHVILLE HWY is 1605 NASHVILLE HWY
1358 LUTZTOWN RD is 1358 LUTZTOWN RD
6 ELM ST is PO BOX 1058
3620 HOWELL FERRY RD is 3620 HOWELL FERRY RD
51 N DUNLAP ST is 51 N DUNLAP ST
116 W MAIN ST is 116 W MAIN ST
59 S MAIN ST is 116 W MAIN ST
505 PARNASSUS AVE is 400 PARNASSUS AVE
400 PARNASSUS

4242 MEDICAL DR is 4242 MEDICAL DR
525 E 68TH ST is 525 E 68TH ST
525 E 68TH ST is 525 E 68TH ST
525 E 68TH ST BOX is 525 E 68TH ST

77
------------------------------------
425 E 61ST ST is 525 E 68TH ST
7777 FOREST LN is 7777 FOREST LN
7777 FOREST LN is 7777 FOREST LN
1600 SW ARCHER RD RM is 1600 SW ARCHER RD
UF HEALTH TEST SITE POP UP 1600 SW ARCHER RD is 1600 SW ARCHER RD
1600 SW ARCHER is 1600 SW ARCHER RD
1600 SW ARCHER RD is 1600 SW ARCHER RD
2000 SW ARCHER RD is 1600 SW ARCHER RD

88
------------------------------------
1301 MEDICAL CTR DR is A1302 MEDICAL CENTER NORTH
23388 MULHOLLAND DR is 23388 MULHOLLAND DR
12368 STRATFORD DR is 12368 STRATFORD DR
2700 E 29TH ST is 2700 E 29TH ST STE 105
120 E BEAUREGARD is 1481 BUTLER DR
120 E BEAUREGARD is 1481 BUTLER DR
5700 N PORTLAND AVE is 5700 N PORTLAND AVE
1401 MEDICAL PKWY is 3705 MEDICAL PKWY STE 570
8440 WALNUT HILL LN is 8440 WALNUT HILL LN

86
------------------------------------
1000 COULLER DR is 1000 S COULTER ST
13657 W MCD

...

------------------------------------
2490 W 26TH AVE is 2150 W 29TH AVE
381 N 9TH AVE is 381 N 9TH AVE
1901 W CLINCH AVE is 1901 CLINCH AVE
95 GRASSLANDS RD is 95 GRASSLANDS RD
5851 W 95TH ST is 5851 W 95TH ST

88
------------------------------------
MEDICAL CTR BLVD is MEDICAL CENTER BOULEVARD
10383 HAGEN RANCH RD is 10383 HAGEN RANCH RD
148 13TH ST is 148 13TH ST
390 BAR HARBOR RD is 390 BAR HARBOR RD
600 N WOLFE ST is 600 N WOLFE ST
600 N WOLFE ST is 600 N WOLFE ST
111 DEVILLE DR is 149 DEVILLE DR

93
------------------------------------
149 DELVILLE DR is 149 DEVILLE DR
700 HIGH ST is 700 HIGH ST
1656 RIVERCHASE BLVD is 1656 RIVERCHASE BLVD
1401 FOULK RD is 1401 FOULK RD
600 N WOLFE ST is 600 N WOLFE ST
308 N UNION AVE is 308 N UNION AVE
1107 N POINT BLVD is 1107 N POINT BLVD
6501 COYLE AVE is 6501 COYLE AVE
6511 COYLE AVE is 6501 COYLE AVE
1001 S GEORGE ST is 1001 S GEORGE ST
400 PARNASSUS AVE is 400 PARNASSUS AVE
10800 KNIGHTS RD is KNIGHTS & RED LION RDS
263 FARMINGTON AVE is 26

9000 FRANKLIN SQUARE DR is 9000 FRANKLIN SQUARE DR
9105 FRANKLIN SQUARE DR is 9000 FRANKLIN SQUARE DR
9105 FRANKLIN SQUARE DR is 9000 FRANKLIN SQUARE DR
456 LOCUST ST is PO BOX 199
2600 GLASGOW AVE is 2600 GLASGOW AVE
39000 BOB HOPE DR is 39000 BOB HOPE DR
1365 CLIFTON RD NE is 1365 CLIFTON RD NE
500 UNIVERSITY DR is PO BOX 850
213 COOPER RD is 213 COOPER RD
326 WASHINGTON ST is 326 WASHINGTON ST
500 N HIATUS RD is 500 N HIATUS RD STE 107
3737 MARKET ST is 3737 MARKET ST 6TH FL
176 N MAIN ST is 215 E MAIN ST
3459 5TH AVE is 3420 5TH AVE
3459 5TH AVE is 3420 5TH AVE
3471 5TH AVE is 3420 5TH AVE
3601 5TH AVE is 3420 5TH AVE
3471 5TH AVE is 3420 5TH AVE
3471 5TH AVE is 3420 5TH AVE
3420 5TH AVE is 3420 5TH AVE
3471 5TH AVE is 3420 5TH AVE
3471 5TH AVE is 3420 5TH AVE
3601 5TH AVE is 3420 5TH AVE
3708 5TH AVE is 3420 5TH AVE
3500 5TH AVE is 3420 5TH AVE
29 N E ST is 29 N EAST ST
1095 RYDAL RD is 1095 RYDAL RD STE 100
3400 SPRUCE ST is 3400 SPRUCE ST
1830 GOOD HOPE RD is 1830 GOOD HOPE RD
5

1874 W HILLSBORO BLVD is 1874 W HILLSBORO BLVD
1874 W HILLSBORO BLVD is 1874 W HILLSBORO BLVD
140 S BEACH ST is 140 S BEACH ST
700 W DAGGETT ST is 700 W DAGGETT ST
180 GREENVILLE AVE is 180 GREENVILLE AVE
73 N MAPLE AVE B is 73 N MAPLE AVE STE B
3421 W 9TH ST is 3421 W 9TH ST
240 WILLIAMSON ST is 240 WILLIAMSON ST
4860 Y ST is 4860 Y ST
4860 Y ST is 4860 Y ST
238 INDIANA ST is PO BOX 486
1200 PLEASANT ST is 1200 PLEASANT ST
2000 OLD W CHESTER PIKE is 2000 OLD W CHESTER PIKE
1597 WASHINGTON PIKE is 1050 BOWER HILL RD STE 204
556 PASSAIC AVE is 556 PASSAIC AVE
111 S 11TH ST is 111 S 11TH ST
9500 EUCLID AVE is 9500 EUCLID AVE
8950 EUCLID AVE is 9500 EUCLID AVE
12 MAIN ST is 12 MAIN ST
17 CENTRE PLAZA DR is 17 CENTRE PLAZA DR
1 APPLEWOOD DR is 1 APPLEWOOD DR
100 E LANCASTER AVE is 100 E LANCASTER AVE
5303 FRANKFORD AVE is 5303 FRANKFORD AVE
833 CHESTNUT ST is 833 CHESTNUT ST
1 BARTOL AVE is 1 BARTOL AVE
125 DOUGHTY ST is 125 DOUGHTY ST STE 280
930 RED ROSE CT is 930 RED ROSE CT
82 RED HILL


94
------------------------------------
CALLE 15 N 24 SANTA JUAN is 24 COND SANTA JUANA
HOSPITAL UNIVERSITARIO DE ADULTOS is 334 CALLE ALBACETE
PLAZA CAROLINA MALL is 1357 AVE ASHFORD
PLAZA LAS AMERICAS is 1357 AVE ASHFORD
TORRE DEL METROPOLITANO is RR 3 BOX 4286
396 CALLE DR LUIS F SALAS is 44 CALLE J
301 UNIVERSITY BLVD is 301 UNIVERSITY BLVD
1750 TREE BLVD is 1750 TREE BLVD
2 ND FLOOR 253 HOSPITAL BELLA VISTA is 1114 CALLE ETHEL MARIN
369 CALLE DE DIEGO is 369 CALLE DE DIEGO
BO TERRANOVA CALLE MARGINAL DEL PARQUE is PO BOX 9132
LAGUNA GARDENS SHOPPING CTR is PO BOX 9132
1321 LUGO AVE is 1321 LUGO AVE
504 MEDICAL CTR BLVD is 7 MEDICAL PKWY
CARRETERA 172 URB TURABO GARDENS is 710 CALLE CHIPRE URB PUERTO NUEVO
1451 AVE ASHFORD is 300 AVE MANUEL DOMENECH

82
------------------------------------
300 AVE DOMENECH is 300 AVE MANUEL DOMENECH

77
------------------------------------
302 AVE DOMENECH is 300 AVE MANUEL DOMENECH
AVE ROOSEVELT is 400 AVE FD ROOSEVELT
PLAYA AZUL CTR LOCAL 4 CARR

1600 N OREGON ST is 1600 N OREGON ST STE 1A
247 3RD AVE is 231 S 3RD ST
231 S 3RD ST is 231 S 3RD ST
20 CALLE BALDORIOTY is BOX 2290
3353 L ST is 3353 L ST
AVE LOMAS VERDES is 1790 PLAZA OLMEDO
243 E BLACKSTOCK RD is PO BOX 170158
419 AVE PONCE DE LEON is 431 AVE PONCE DE LEON
735 AVE PONCE DE LEON TORRE AUXI is 735 AVE PONCE DE LEON
PONCE DE LEON AVE is 735 AVE PONCE DE LEON
611 CALLE MAUEL PAVIA is 825 CALLE MARTI APT PH-5
174 CALLE LUIS BARRERAS S is 174 CALLE LUIS BARRERAS S
1015 SE 17TH ST is 1015 SE 17TH ST
7810 CALLE NAZARET is 7810 CALLE NAZARET

95
------------------------------------
404 AVE GENERAL VALERO is 410 AVE GENERAL VALERO
HOSP DR I GONZALEZ MARTINEZ is PMB 192 BOX 703
SUITE 609 TORRE AUXILIO MUTUO is 732 AVE PONCE DE LEON
PONCE DE LEON AVE is 732 AVE PONCE DE LEON
1717 N E ST is 1717 N E ST STE 300
66 CALLE SANTA CRUZ is 66 CALLE SANTA CRUZ
369 CALLE DE DIEGO is 369 CALLE DE DIEGO
1150 CAMPO SANO AVE is 1150 CAMPO SANO AVE
151 NW 11 ST is 151 NW 11TH ST STE E102
64 

In [14]:
CHECK = pd.DataFrame(dicts).sort_values('SCORE').drop_duplicates('ME', keep='last')

In [15]:
NEW_PHONES = pd.merge(CHECK[CHECK.PHONE=='None'], phoney, on=['ME','adrs_id']).drop_duplicates('ME')
NEW_PHONES['PHONE']=NEW_PHONES.phn_numbr

In [16]:
maybe = pd.concat([CHECK[CHECK.PHONE!='None'],NEW_PHONES[CHECK.columns]])
maybe['phone_number'] = [use.fix_phone(x) for x in maybe.PHONE]

In [17]:
yeah = pd.merge(bolos, maybe, on=['ME','comm_id'], how='left')[['entity_id', 'me#', 'comm_id', 'usage', 'load_type_ind', 'addr_type',
       'addr_line_1', 'addr_line_2', 'addr_line_3', 'addr_city', 'addr_state', 'addr_zip',
       'addr_plus4', 'addr_country', 'source', 'source_dtm', 'phone_number']]

In [19]:
BOLOS = pd.read_csv(bolo_file, sep='|')
BOLOS['me#'] = use.fix_me(BOLOS['me#'])
BOLOS['ME'] = use.fix_me(BOLOS['me#'])

In [20]:
pd.merge(BOLOS, maybe, on=['ME','comm_id'])[['entity_id', 'me#', 'comm_id', 'usage', 'load_type_ind', 'addr_type',
       'addr_line_1', 'addr_line_3', 'addr_line_2', 'addr_city', 'addr_state',
       'addr_zip', 'addr_plus4', 'addr_country', 'source', 'source_dtm', 'phone_number']]

entity_id          me#   comm_id usage load_type_ind addr_type  \
0       10000584  04501810717  21494436    PO             R        OF   
1       10000818  04501810938   7356840    PO             R        OF   
2       10000961  04501811055  27146067    PO             R        OF   
3       10001247  04501811292   6806473    PO             R        OF   
4       10001494  04501811519  11833143    PO             R        OF   
...          ...          ...       ...   ...           ...       ...   
64573    9998556  04501800908  27179671    PO             R        OF   
64574    9998608  04501800941  27172468    PO             R        OF   
64575    9998712  04501801025  19575170    PO             R        OF   
64576    9998946  04501801211  27131986    PO             R        OF   
64577    9999440  04501801602  27091824    PO             R        OF   

                                    addr_line_1                 addr_line_3  \
0                                           NaN   COLUMBIA HEART CLINIC, PA   
1                     COLUMBIA GASTROENTEROLOGY                      STE 1A   
2                    LABORATORY DIR/PATHOLOGIST         LAB DIR/PATHOLOGIST   
3                 MCLEOD FAMILY MEDICINE-WILSON         701 CASHUA FERRY RD   
4                     ROCK HILL GYNECOLOGY & OB   ROCK HILL GYNECOLOGY & OB   
...                                         ...                         ...   
64573              UNIVERSITY MD MEDICAL SYSTEM                       STE 2   
64574                                       NaN  MEDICAL BILLING MANAGEMENT   
64575  LIMITED TO OFFICIAL GOVERNMENT DUTIES ON                     STE 100   
64576                                       NaN      FLORIDA EYE ASSOCIATES   
64577       LIMITED TO OFFICIAL DUTIES FOR MUSC                      RM 218   

                              addr_line_2    addr_city addr_state addr_zip  \
0      8 RICHLAND MEDICAL PARK DR STE 300     COLUMBIA         SC    29203   
1                          2739 LAUREL ST     COLUMBIA         SC    29204   
2                       4220 HARDING PIKE    NASHVILLE         TN    37205   
3                              PO BOX 811   DARLINGTON         SC    29540   
4             1721-05 EBENEZER RD STE 145    ROCK HILL         SC    29732   
...                                   ...          ...        ...      ...   
64573                    3531 FASHION WAY     TORRANCE         CA    90503   
64574                    2525 DESALES AVE  CHATTANOOGA         TN    37404   
64575                    2160 FOUNTAIN DR   SNELLVILLE         GA    30078   
64576                   161 MALABAR RD NE     PALM BAY         FL    32907   
64577                      171 ASHLEY AVE   CHARLESTON         SC    29425   

       addr_plus4  addr_country source                  source_dtm  \
0             NaN           NaN    ASM  2022-01-20 03:03:23.209509   
1             NaN           NaN    ASM  2022-01-20 03:03:23.209509   
2             NaN           NaN    ASM  2022-01-20 03:03:23.209509   
3             NaN           NaN    ASM  2022-01-20 03:03:23.209509   
4             NaN           NaN    ASM  2022-01-20 03:03:23.209509   
...           ...           ...    ...                         ...   
64573         NaN           NaN    ASM  2022-01-20 03:03:23.209509   
64574         NaN           NaN    ASM  2022-01-20 03:03:23.209509   
64575         NaN           NaN    ASM  2022-01-20 03:03:23.209509   
64576         NaN           NaN    ASM  2022-01-20 03:03:23.209509   
64577         NaN           NaN    ASM  2022-01-20 03:03:23.209509   

      phone_number  
0       8032566511  
1       8037994800  
2       6152723025  
3       8437771100  
4       8033282401  
...            ...  
64573   3109741260  
64574   4234954325  
64575   3342392622  
64576   3217272020  
64577   8437921414  

[64578 rows x 17 columns]

In [21]:
from datetime import date
today = str(date.today())
pd.merge(BOLOS, maybe, on=['ME','comm_id'])[['entity_id', 'me#', 'comm_id', 'usage', 'load_type_ind', 'addr_type',
       'addr_line_1', 'addr_line_3', 'addr_line_2', 'addr_city', 'addr_state',
       'addr_zip', 'addr_plus4', 'addr_country', 'source', 'source_dtm', 'phone_number']].to_csv(f'../../Data/PhoneAppend/ADDRESS_SCORING_BATCH_{today}_PHONE_APPEND.txt', sep='|', index=False)

In [23]:
len(maybe)/len(BOLOS)

0.19223762234764594

In [24]:
maybe

ME                    adrs_id   comm_id            GOV_ADDR  \
61439  05605130226  WA988620000WI1116X1116101  28001251                1116   
55487  04203120643  PR009860001CACARRECARR101  28068821           CARRETERA   
88921  04203800628  PR009350000RIASEMXASEM101  27830560                ASEM   
10623  74801900236  NC271570001WIMEDICBLVD300  19364112    MEDICAL CTR BLVD   
85226  03601953420  NC275876526WA11635DRXX300  20419466  11635 NORTHPARK DR   
...            ...                        ...       ...                 ...   
34913  04202110466  FL331762118MI8900XDRXX400  27849267   8900 N KENDALL DR   
34914  04201110519  FL328197829OR6001XRDXX309  27982764    6001 VINELAND RD   
34915  03548111128  NY110303816MA300XXDRXX300  27914386    300 COMMUNITY DR   
34916  03547111086  CA951243908SA2425XDRXX300  27934544   2425 SAMARITAN DR   
34917  03547111141  CT068246017FA52XXXRDXX300  27790942         52 BEACH RD   

               BOLO_ADDR GOV_ZIP BOLO_ZIP  SCORE        PHONE phone_number  
61439         PO BOX 549   98862    98862      0  5.09997e+09   5099968180  
55487        PO BOX 9784   00986    00674      0  8.09769e+09   8097692477  
88921       PO BOX 29134   00935    00929      0  7.87777e+09   7877773535  
10623              27157   27157    27157      0  3.36716e+09   3367162734  
85226               #200   27587    27614      0  9.19571e+09   9195706060  
...                  ...     ...      ...    ...          ...          ...  
34913  8900 N KENDALL DR   33176    33176    100  7.86596e+09   7865961960  
34914   6001 VINELAND RD   32819    32819    100  4.07931e+09   4079306684  
34915   300 COMMUNITY DR   11030    11030    100  5.16562e+09   5165624458  
34916  2425 SAMARITAN DR   95124    95124    100  4.08559e+09   4085592011  
34917        52 BEACH RD   06824    06824    100   2.0326e+09   2032597871  

[64578 rows x 10 columns]

In [19]:
len(bolos)

301551

In [20]:
len(maybe)/len(bolos)

0.0826062589744355